# One-Hot Recurrent Model

Using the balanced data.

Set whether the model looks at abstracts or titles here:

In [ ]:
# 'abstract' or 'title'
text_field = 'title'
assert text_field in ('abstract', 'title'), 'text_field must be one of title or abstract.'

[autoreload of arxiv_vixra_models.models failed: Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/IPython/extensions/autoreload.py", line 247, in check
    superreload(m, reload, self.old_objects)
NameError: name 'LightningModule' is not defined
]


# Imports and Setup

Imports and colab setup

In [ ]:
%%capture import_capture --no-stder
# Jupyter magic methods
# For auto-reloading when external modules are changed
%load_ext autoreload
%autoreload 2
# For showing plots inline
%matplotlib inline

# pip installs needed in Colab for arxiv_vixra_models
!pip install wandb --upgrade
# v1.5.0 of pl breaks wandb sweeps:
# https://github.com/PyTorchLightning/pytorch-lightning/issues/10336
!pip install pytorch-lightning==1.4.9
!pip install unidecode
# Update sklearn
!pip uninstall scikit-learn -y
!pip install -U scikit-learn

import math
import pandas as pd
import numpy as np
import torch
import matplotlib.pyplot as plt
pd.set_option(u'float_format', '{:f}'.format)

# pl and wandb installation and setup.
from pytorch_lightning import Trainer
from pytorch_lightning.loggers import WandbLogger
import wandb

`wandb` log in:

In [ ]:
wandb.login()

[autoreload of arxiv_vixra_models.models failed: Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/IPython/extensions/autoreload.py", line 247, in check
    superreload(m, reload, self.old_objects)
NameError: name 'LightningModule' is not defined
]
wandb: WARNING Calling wandb.login() after wandb.init() has no effect.


True

Google drive access

In [ ]:
# Give the notebook access to the rest of your google drive files.
from google.colab import drive
drive.mount("/content/drive", force_remount=True)
# Enter the relevant foldername
FOLDERNAME = '/content/drive/My Drive/ML/arxiv_vixra'
assert FOLDERNAME is not None, "[!] Enter the foldername."
# For importing modules stored in FOLDERNAME or a subdirectory thereof:
import sys
sys.path.append(FOLDERNAME)

Mounted at /content/drive


Import models, loaders, and utility functions from an external package:

In [ ]:
import arxiv_vixra_models as avm

Computing specs. Save the number of processors to pass as `num_workers` into the Datamodule and cuda availability for other flags.

In [ ]:
# GPU. Save availability to is_cuda_available.
gpu_info= !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
  is_cuda_available = False
else:
  print(f"GPU\n{50 * '-'}\n", gpu_info, '\n')
  is_cuda_available = True

# Memory.
from psutil import virtual_memory, cpu_count
ram_gb = virtual_memory().total / 1e9
print(f"Memory\n{50 * '-'}\n", 'Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb), '\n')

# CPU.
print(f"CPU\n{50 * '-'}\n",f'CPU Processors: {cpu_count()}')
# Determine the number of workers to use in the datamodule
num_processors = cpu_count()

GPU
--------------------------------------------------
 Tue Nov  9 02:43:07 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 495.44       Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   39C    P0    39W / 300W |   5341MiB / 16160MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                

Copy data to cwd for speed.

In [ ]:
train_data_file_name = 'balanced_filtered_normalized_data_train.feather'
val_data_file_name = 'balanced_filtered_normalized_data_validation.feather'
SUBDIR = '/data/data_splits/'
train_data_path = FOLDERNAME + SUBDIR + train_data_file_name
val_data_path = FOLDERNAME + SUBDIR + val_data_file_name
chars_file_name = 'normalized_char_set.feather'
chars_path = FOLDERNAME + SUBDIR + chars_file_name
!cp '{train_data_path}' .
!cp '{val_data_path}' .
!cp '{chars_path}' .

In [ ]:
train_data_df = pd.read_feather(train_data_file_name)
val_data_df = pd.read_feather(val_data_file_name)
chars_df = pd.read_feather(chars_file_name)

Use notebook name as `wandb` `project` string. Remove the file extension and any "Copy of" or "Kopie van" text which arises from copying notebooks and running in parallel.

In [ ]:
from requests import get
project_str = get('http://172.28.0.2:9000/api/sessions').json()[0]['name']
project_str = project_str.replace('.ipynb', '').replace('Kopie%20van%20', '').replace('Copy%20of%20', '')
print(project_str)

balanced_title_one_hot_recurrent


# Validation Set Filtering

Filter any overlap between the training and validation datasets. Most complete duplicates should have been filtered, but some may not have evaluated as equal prior to text normalization or because they only coinicided in one of the two text columns (e.g., there are distinct papers which share the same title but have different abstracts in the dataset).  We perform strict filtering below.

In [ ]:
val_data_intersections_filtered_df = val_data_df.merge(train_data_df, on=[text_field], how='outer', suffixes=['', '_'], indicator=True).loc[lambda x: x['_merge'] == 'left_only'].iloc[:,:3]
print(f'{len(val_data_df) - len(val_data_intersections_filtered_df)} items removed from val set, {100 * (len(val_data_df) - len(val_data_intersections_filtered_df)) / len(val_data_df):.3f} percent.')

42 items removed from val set, 0.558 percent.


Inspect datasets using `print` and `to_string()` to avoid colab javascript errors

In [ ]:
print(train_data_df.head().to_string())

                                                                                         title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [ ]:
print(val_data_intersections_filtered_df.head().to_string())

                                                                                 title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    abstract source
0                             

# Model Testing

Setting hyperparameters and performing a small test run.

Dictionary args for model and datamodule.

In [ ]:
# Data was prepared with a max of 2048 chars for abstracts and 128 for titles.
seq_len = 2048 if text_field == 'abstract' else 128
model_args_dic = {'seq_len': seq_len,
              'num_layers': 3,
              'bidirectional': True,
              'rnn_type': 'GRU',
              'hidden_size': 128,
              'chars': chars_df,
              }
              
# The batch size we set here determines the number of datapoints used
# in the histogram that avm.WandbEmbeddingTextCallback logs
data_args_dic = {'seq_len': seq_len,
                 'train_data': train_data_df,
                 'val_data': val_data_intersections_filtered_df,
                 'chars': chars_df, 
                 'text_column': text_field,
                 'num_workers': num_processors,
                 'batch_size': 512,
                 'pin_memory': is_cuda_available,
                 'persistent_workers': True
                 }

Small test run.

In [ ]:
small_example_data_module = avm.OneHotCharDataModule(**{**data_args_dic, **{'sample_size': data_args_dic['batch_size']}})
small_example_data_module.setup()
small_example_loader = small_example_data_module.train_dataloader()
small_example_inputs, small_example_targets = next(iter(small_example_loader))
# Print the first few input texts
for tensor, source in zip(small_example_inputs[:3], small_example_targets[:3]):
    stripped_text = avm.one_hot_decoding(tensor, chars_df)
    print(f"text: {stripped_text}",
          f'len: {len(stripped_text)}',
          f'source: {source.item()}',
          sep='\n')
small_example_model = avm.LitOneHotCharRecurrent(**model_args_dic)
small_example_preds, small_example_losses, _ = small_example_model.preds_losses_hiddens(small_example_inputs, small_example_targets)
print('\npreds shape:', small_example_preds.shape, '\n')
print('\nactual loss:', small_example_losses.item(), '\n')
print('\nexpected approx loss', -math.log(.5), '\n')

text: the e - and b - modes in the cmb
len: 32
source: 1
text: deep space transport with field effect of vacuum stress energy
len: 62
source: 1
text: ergonomization attitudes in general aviation
len: 44
source: 1
128

preds shape: torch.Size([512, 1]) 


actual loss: 0.6934786438941956 


expected approx loss 0.6931471805599453 



For logging purposes, take another sample from the validation set which will be be used to visualize predictions.

In [ ]:
val_sample  = next(iter(small_example_data_module.val_dataloader()))
val_sample_text = [avm.one_hot_decoding(input, chars_df) for input in val_sample[0]]
print(*val_sample_text[:3], sep='\n')

triggered di - hadron correlations in pb - - pb collisions from the alice experiment
unified nuclear core activity map reconstruction using heterogeneous instruments with data assimilation
anomaly cancellations on lower - dimensional hypersurfaces by inflow from the bulk


# `wandb` Hyperparameter Tuning



Set fixed hyperparameters and the configuration file for the `wandb` sweep.  Notes on the setup below:
* In `sweep_config['parameters']` we only include those parameters which are to be swept over.
* All fixed parameters will put in `fixed_hyperparam_dic`.
* `fixed_hyperparam_dic` is eventually merged with the hyperparameter dictionary for those hyperparameters included in `sweep_config` which is generated by `wandb`, with the result passed to the model.
* It is simplest to only sweep over hyperparameters which don't change the size of the model so that we can optimize with a single `batch_size`.  This also helps prevent `CUDA` memory errors which can occur if the sweep generates a model which is too large for the given `batch_size`.
* Pass a `count: int` arg to `wandb.agent` to limit the number of models trained. Without, the training runs indefinitely.

In [ ]:
fixed_hyperparam_dic = {'seq_len': seq_len,
                        'rnn_type': 'GRU',
                        'num_layers': 3,
                        'bidirectional': True,
                        'hidden_size': 256,
                        'truncated_bptt_steps': None,
                        'chars': chars_df,
                        'fc_dropout': None,
                        'recurrent_dropout': None
                        }

sweep_config = {'method': 'random'}
sweep_config['early_terminate'] = {'type': 'hyperband',
                                    'min_iter': 3
                                   }
sweep_config['metric'] = {'name': 'best_val_loss',
                           'goal': 'minimize'
                           }
sweep_config['parameters'] =  {'lr': {'distribution': 'log_uniform',
                                      'min': math.log(1e-5),
                                      'max': math.log(1e-2)
                                      },                          
                               }

Re-instantiate data using the full dataset and a non-trivial batch size.  Implement truncated backpropagation through time, if desired, and set the `max_epochs` of the run and other desired parameters in dictionary for the trainer, which is also appended to `fixed_hyperparam_dic` for logging purposes.

In [ ]:
# Setting 'batch_size' in data_args_dic controls the batch size, while setting
# this key in fixed_hyperparam_dic just lets wandb track this hyperparameter.
data_args_dic['batch_size'] = fixed_hyperparam_dic['batch_size'] = 512 #2 **10


# Set max_epochs in a dict, along with any other optional trainer kwargs.
trainer_dic = {'max_epochs': 32,
               'stochastic_weight_avg': True
               }
# Merge trainer_dic into fixed_hyperparam_dic for logging purposes.
fixed_hyperparam_dic = {**fixed_hyperparam_dic, **trainer_dic}

def sweep_iteration():
    # Group by various properties
    group_str_elements = [fixed_hyperparam_dic['rnn_type'],
                          f"{'-bidirectional' if fixed_hyperparam_dic['bidirectional'] else ''}",
                          f"-hidden_size_{fixed_hyperparam_dic['hidden_size']}"
                          f"-{fixed_hyperparam_dic['num_layers']}_layers",
                          f"-{fixed_hyperparam_dic['max_epochs']}_epochs"]
    group_str = ''.join(group_str_elements)
    with wandb.init(group=group_str) as run:
        data = avm.OneHotCharDataModule(**data_args_dic)
        config = wandb.config
        # Merge config into remaining parameters.
        config = {**fixed_hyperparam_dic, **config}
        model = avm.LitOneHotCharRecurrent(**config)
        # Overwrite the random run names chosen by wandb.
        name_str_elements = [f"lr_{config['lr']:.3E}",
                             f"{'-fc_dropout_' + str(config['fc_dropout']) if config['fc_dropout'] else ''}",
                             f"{'recurrent_-dropout_' + str(config['recurrent_dropout']) if config['recurrent_dropout'] else ''}"]
        name_str = ''.join(name_str_elements)
        run.name = name_str
        trainer = Trainer(
            logger=WandbLogger(),
            gpus=-1 if is_cuda_available else 0,
            log_every_n_steps=5,
            callbacks=[avm.WandbTextCallback(val_sample=val_sample,
                                             decoder_fn=avm.one_hot_decoding,
                                             translation_data=chars_df,
                                             labels=('arxiv', 'vixra'))],
            num_sanity_val_steps=-1,
            **trainer_dic
            )
        trainer.fit(model, datamodule=data)

In [ ]:
sweep_id = wandb.sweep(sweep_config, project=project_str)

Create sweep with ID: 3p5e84gx
Sweep URL: https://wandb.ai/garrett361/balanced_title_one_hot_recurrent/sweeps/3p5e84gx


In [ ]:
wandb.agent(sweep_id, function=sweep_iteration)

wandb: Agent Starting Run: xll27xdp with config:
wandb: 	lr: 0.007836400107599504


128


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
wandb: WARNING Config item 'lr' was locked by 'sweep' (ignored update).

  | Name        | Type     | Params
-----------------------------------------
0 | train_acc   | Accuracy | 0     
1 | val_acc     | Accuracy | 0     
2 | test_acc    | Accuracy | 0     
3 | rnn         | GRU      | 2.9 M 
4 | class_layer | Linear   | 513   
-----------------------------------------
2.9 M     Trainable params
0         Non-trainable params
2.9 M     Total params
11.473    Total estimated model params size (MB)


Validation sanity check: 0it [00:00, ?it/s]

Training: -1it [00:00, ?it/s]

...

128


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
wandb: WARNING Config item 'lr' was locked by 'sweep' (ignored update).

  | Name        | Type     | Params
-----------------------------------------
0 | train_acc   | Accuracy | 0     
1 | val_acc     | Accuracy | 0     
2 | test_acc    | Accuracy | 0     
3 | rnn         | GRU      | 2.9 M 
4 | class_layer | Linear   | 513   
-----------------------------------------
2.9 M     Trainable params
0         Non-trainable params
2.9 M     Total params
11.473    Total estimated model params size (MB)


Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_plot/confusion_matrix.py:125: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots()
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_plot/roc_curve.py:122: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots()
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_plot/precision_recall_curve.py:139: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until exp

Training: -1it [00:00, ?it/s]